### **1. IMPORT LIBRARY**

In [1]:
# Standard library imports
from datetime import datetime, timedelta

# Third-party library imports
import numpy as np
import pandas as pd
import xlsxwriter
from ydata_profiling import ProfileReport

### **2. ACQUIRE DATA**
- **Note**: D:\Team EcoByte\ to your directory

In [2]:
customer = pd.read_excel(r"D:\Team EcoByte\data.xlsx", sheet_name="customer")
ticket = pd.read_excel(r"D:\Team EcoByte\data.xlsx", sheet_name="ticket")
film = pd.read_excel(r"D:\Team EcoByte\data.xlsx", sheet_name="film")

### **3. ANALYZE DATA**

In [3]:
customer_report = ProfileReport(customer)
customer_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
ticket_report = ProfileReport(ticket)
ticket_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
film_report = ProfileReport(film)
film_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### **4. WRANGLE DATA**

#### **A. FUNCTIONS**

**SHARED FUNCTION**

In [6]:
def remove_special_character(str):
    special_character = '.,/\_'
    return str.strip(special_character)

def to_lower(string):
    return str.lower(string)
    
def to_title(string):
    return string.title()

def to_upper(string):
    return str.upper(string)

In [7]:
def format_data_in_column(dataframe, column):
    dataframe[column] = dataframe[column].apply(to_lower)
    dataframe[column] = dataframe[column].apply(to_title)
    return dataframe

In [8]:
def handle_special_character_in_column(dataframe):
    for column in dataframe.columns:
        dataframe[column] = dataframe[column].astype(str)
        dataframe[column] = dataframe[column].apply(remove_special_character)
    return dataframe

In [9]:
def replace_column_values(dataframe, column, dict):
    dataframe[column] = dataframe[column].replace(dict)
    return dataframe

**CUSTOMER TABLE FUNCTION**

In [10]:
def get_age(year):
    return 2019-int(year)

In [11]:
def handle_wrong_age_based_on_job(age):
    average_age_teenager = (19 + 13)//2
    if age < 10:
        return average_age_teenager
    return age
    
def reformat_wrong_age_to_datetime(dob):
    average_age_teenager = (19 + 13)//2
    dob = datetime.strptime(dob, "%m-%d-%Y")
    if (2019-dob.year) < 10:
        formated_dob = dob.replace(month = 1, day = 1, year = 2019-average_age_teenager)
        return formated_dob
    return dob

In [12]:
def convert_timestamp_to_datetime(dataframe, column_name):
    for index, row in dataframe.iterrows():
        py_date = datetime(1899, 12, 31) + timedelta(days=row[column_name])
        formatted_date = py_date.strftime('%m-%d-%Y')        
        dataframe.loc[index, column_name] = formatted_date
    
    return dataframe

In [13]:
def get_generation(dob):
    dob = str(dob)
    dob = datetime.strptime(dob, "%Y-%m-%d %H:%M:%S")
    gen = ''
    if 1997 <= dob.year <= 2013:
        gen = 'Gen Z'
    elif 1980 <= dob.year <= 1996:
        gen = 'Gen Y'
    elif 1964 <= dob.year <= 1979:
        gen = 'Gen X'
    return gen

**FILM TABLE FUNCTION**

In [14]:
def replace_special_characters(dataframe, column, replace_dict):
    for old, new in replace_dict.items():
        dataframe[column] = dataframe[column].str.replace(old, new)
    return dataframe

#### **B. PROCESS TABLE**

**CUSTOMER TABLE**

In [15]:
customer.fillna('', inplace=True)

In [16]:
customer = handle_special_character_in_column(customer)

In [17]:
customer["DOB"] = customer["DOB"].astype("int64")

In [18]:
customer = convert_timestamp_to_datetime(customer, "DOB")

C:\Users\DELL\AppData\Local\Temp\ipykernel_7692\69919905.py:5: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '04-19-1999' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  dataframe.loc[index, column_name] = formatted_date


In [19]:
customer["DOB"]

0       04-19-1999
1       04-17-1998
2       12-17-1993
3       11-09-1999
4       10-02-1994
           ...    
4474    07-06-1995
4475    01-02-2001
4476    06-18-1988
4477    09-09-1996
4478    04-27-2002
Name: DOB, Length: 4479, dtype: object

In [20]:
customer['Age'] = customer['DOB'].str[-4:]
customer['Age'] = customer['Age'].astype(int)

In [21]:
customer['Age'] = customer['Age'].apply(get_age)
customer.insert(2, 'Age', customer.pop('Age'))

In [22]:
customer["Age"] = customer["Age"].apply(handle_wrong_age_based_on_job)

In [23]:
customer["DOB"] = customer["DOB"].apply(reformat_wrong_age_to_datetime)

In [24]:
customer['DOB'] = pd.to_datetime(customer['DOB'], format='%Y-%m-%d %H:%M:%S')

In [25]:
customer["Gen"] = customer["DOB"].apply(get_generation)

In [26]:
gender_dict = {"Nam":"Male", "Nữ":"Female"}
customer = replace_column_values(customer, "gender", gender_dict)

In [27]:
column_to_format_in_customer = ["address", "job", "industry"]

In [28]:
for column in column_to_format_in_customer:
    customer = format_data_in_column(customer, column)

**TICKET TABLE**

In [29]:
ticket.fillna('', inplace=True)

C:\Users\DELL\AppData\Local\Temp\ipykernel_7692\3111854558.py:1: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  ticket.fillna('', inplace=True)


In [30]:
ticket = handle_special_character_in_column(ticket)

In [31]:
ticket['saledate'] = ticket['saledate'].astype(str)

In [32]:
ticket['saledate'] = ticket['saledate'].fillna('')

In [33]:
ticket["saledate"] = pd.to_datetime(ticket["saledate"])
ticket["date"] = pd.to_datetime(ticket["date"])
ticket["ticket price"] = ticket["ticket price"].astype("int64")

In [34]:
slot_type_dict = {"ĐƠN" : "SINGLE", "ĐÔI" : "COUPLE"}
ticket_type_dict = {"Thành viên" : "Member"}
popcorn_dict = {"Có" : "Yes", "Không" : "No"}
film_dict = {
    "(LT) DORAEMON: NOBITA VÀ MẶT TRĂNG PHIÊU LƯU KÝ (G)" : "Doraemon: Nobita's Chronicle of the Moon Exploration",
    "(PĐ) DORAEMON: NOBITA VÀ MẶT TRĂNG PHIÊU LƯU KÝ (G)" : "Doraemon: Nobita's Chronicle of the Moon Exploration",
    "ALADDIN (LT) (G)" : "Aladdin (2019)",
    "ALADDIN (PD) (G)" : "Aladdin (2019)",
    "AVENGERS: HỒI KẾT" : "Marvel Studios' Avengers: Endgame",
    "CHÚA TỂ GODZILLA: ĐẾ VƯƠNG BẤT TỬ (C13)" : "Godzilla: King of the Monsters",
    "CORGI: NHỮNG CHÚ CHÓ HOÀNG GIA (LT)" : "The Queen's Corgi",
    "JOHN WICK 3: CHUẨN BỊ CHIẾN TRANH (C18)" : "John Wick: Chapter 3 – Parabellum",
    "MẸ MA THAN KHÓC LA LLORONA (C18)" : "The Curse Of La Llorona",
    "NGÔI ĐỀN KỲ QUÁI (C18)" : "Pee Nak",
    "NỤ HÔN MA QUÁI (C18)" : "Krasue: Inhuman Kiss",
    "POKÉMON: THÁM TỬ PIKACHU (C13)" : "Pokémon: Detective Pikachu",
    "QUÝ CÔ LỪA ĐẢO" : "The Hustle",
    "THẰNG EM LÝ TƯỞNG" : "Inseparable Bros",
    "VÔ GIAN ĐẠO (C18)" : "Infernal Affairs",
    "VỢ BA" : "The Third Wife",
    "ƯỚC HẸN MÙA THU" : "Autumn Promise",
    "CÀ CHỚN ANH ĐỪNG ĐI" : "Cà Chớn, Anh Đừng Đi",
    "LẬT MẶT: NHÀ CÓ KHÁCH" : "Face Off: The Walking Guests",
}

In [35]:
ticket = replace_column_values(ticket, "slot type", slot_type_dict)
ticket = replace_column_values(ticket, "ticket type", ticket_type_dict)
ticket = replace_column_values(ticket, "popcorn", popcorn_dict)
ticket = replace_column_values(ticket, "film", film_dict)

**FILM TABLE**

In [36]:
film.fillna('', inplace=True)

In [37]:
film = handle_special_character_in_column(film)

In [38]:
column_to_format_in_film = ["director", "cast"]

In [39]:
for column in column_to_format_in_film:
    film = format_data_in_column(film, column)

In [40]:
director_dict = {'Ã¯' : 'ï', 'Ã¸' : 'ø'}
cast_dict = {'ã¯C' : 'ïc'}
description_dict = {'â€œX' : '', 'â€“' : '', 'â€' : 'ese', 'Ã¯' : 'ï', 'â€™' : ''}

In [41]:
film = replace_special_characters(film, "director", director_dict)
film = replace_special_characters(film, "cast", cast_dict)
film = replace_special_characters(film, "description", description_dict)

In [42]:
film.rename(columns={"title":"film"},inplace=True)

#### **C. MERGE TABLE**

In [43]:
merge_ticket_film = pd.merge(ticket, film, on='film', how='inner')

In [44]:
merge_ticket_film_customer = pd.merge(merge_ticket_film, customer, on='customerid', how='inner')

##### **SHARED FUNCTION FOR GENERAL AND DETAIL**

In [45]:
def turn_column_name_into_same_format(dataframe):
    for column in dataframe.columns:
        new_column = column.lower()
        new_column = new_column.replace(' ', '_')
        dataframe = dataframe.rename(columns={column:new_column})
    return dataframe

#### **D. CREATE GENERAL AND DETAIL DATAFRAME**
- **GENERAL**: Analyze sales performance and customer demographics of the cinema in general.
- **DETAIL**: Analyze sales performance and customer behavior in details.

##### **GENERAL FUNCTION**

In [46]:
def assign_group_based_on_count(dataframe, list_group, list_count):
    for i in dataframe.index:
        index = list_group.index(dataframe.loc[i, "Merged_Column"])
        if dataframe.loc[i, "slot type"] == 'SINGLE':
            if list_count[index] == 1:
                dataframe.loc[i, 'Group'] = 'Alone'
            elif list_count[index] == 2:
                dataframe.loc[i, 'Group'] = '2 people'
            elif list_count[index] > 2:
                dataframe.loc[i, 'Group'] = 'More than 2 people'
        else:
            if list_count[index] == 1:
                dataframe.loc[i, 'Group'] = '2 people'
            elif list_count[index] >= 2:
                dataframe.loc[i, 'Group'] = 'More than 2 people'
    return dataframe

##### **DETAIL FUNCTION**

In [47]:
def convert_to_pd_datetime(dt):
    try:
        pd_dt = pd.to_datetime(dt, format='%Y-%m-%d %H:%M:%S')
        return pd_dt
    except Exception as e:
        print(f"Error occurred: {e}")
        return pd.NaT

In [48]:
def calculate_time_difference_to_minute(dataframe):
    dataframe['time_diff'] = (dataframe['date_time'] - dataframe['saledate']).dt.total_seconds()
    dataframe["time_diff_minute"] = dataframe["time_diff"] / 60
    dataframe["time_diff_minute"] = dataframe["time_diff_minute"].fillna(0)
    dataframe["time_diff_minute"] = dataframe["time_diff_minute"].astype(int)
    return dataframe

In [49]:
def calculate_customer(slot_type):
    if slot_type == 'SINGLE':
        return 1
    elif slot_type == 'COUPLE':
        return 2

In [50]:
def merge_lists_without_duplicates(list1, list2):
    set1 = set(list1)
    set2 = set(list2)
    merged_set = set1.union(set2)
    merged_list = list(merged_set)
    return merged_list

In [51]:
def create_list_in_column(row, list_in):
    if list_in == 'Adventure' or list_in == 'Action':
        return 0 if 'Action-Adventure' in row['listed_in'] else (1 if list_in in row['listed_in'] else 0)
    else:
        if row['slot_type'] == 'SINGLE':
            return 1 if list_in in row['listed_in'] else 0
        elif row['slot_type'] == 'COUPLE':
            return 2 if list_in in row['listed_in'] else 0
        else:
            return 0

In [52]:
def get_hour(time_str):
    hour, minute, second = time_str.split(":")
    return int(hour)

In [53]:
def create_ticket_column(row, ticket):
    if row['ticket_price'] == ticket: return 1
    else: return 0

In [54]:
def calculate_retention_rate(dataframe):
    dataframe['retention_rate'] = 0
    for cohort_week in dataframe['cohort_week'].unique():
        cohort_size = dataframe[dataframe['cohort_week'] == cohort_week]['customerid'].nunique()
        cohort_week_data = dataframe[dataframe['cohort_week'] == cohort_week]
        for week in cohort_week_data['week'].unique():
            retention_rate = cohort_week_data[cohort_week_data['week'] == week]['customerid'].nunique() / cohort_size
            dataframe.loc[(dataframe['cohort_week'] == cohort_week) & (dataframe['week'] == week), 'retention_rate'] = retention_rate
    return dataframe

###### **CREATE COPY MERGE TABLE**

In [ ]:
#merge_ticket_film_customer_copy = merge_ticket_film_customer

**CREATE GENERAL DATAFRAME**

In [55]:
merge_ticket_film_customer['date'] = merge_ticket_film_customer['date'].astype(str)

In [59]:
merge_ticket_film_customer['Merged_Column'] = merge_ticket_film_customer["orderid"]+ " " + merge_ticket_film_customer['customerid'] + ' ' + merge_ticket_film_customer['date'] + ' ' + merge_ticket_film_customer['time'] + ' ' + merge_ticket_film_customer['film'] +  ' ' + merge_ticket_film_customer["slot type"]

In [60]:
list_group = list(merge_ticket_film_customer.groupby('Merged_Column').groups.keys())
list_count = list(merge_ticket_film_customer.groupby('Merged_Column')["customerid"].count())

In [61]:
merge_ticket_film_customer = assign_group_based_on_count(merge_ticket_film_customer, list_group, list_count)

In [62]:
general = pd.DataFrame(merge_ticket_film_customer[["saledate", "orderid", "ticketcode", "ticket price", "customerid", "Gen", "Age", "job", "Group", "film", "listed_in", "country", "total", "cashier"]])

In [63]:
general = turn_column_name_into_same_format(general)

In [65]:
general.to_excel(r"D:\Data\Check\general.xlsx",index=False)

**CREATE DETAIL DATAFRAME**

In [66]:
merge_ticket_film_customer["saledate"] = pd.to_datetime(merge_ticket_film_customer["saledate"])

In [67]:
merge_ticket_film_customer["date_time"] = merge_ticket_film_customer["date"] + ' ' + merge_ticket_film_customer["time"]

In [68]:
merge_ticket_film_customer["date_time"] = merge_ticket_film_customer["date_time"].apply(convert_to_pd_datetime)

In [69]:
merge_ticket_film_customer = calculate_time_difference_to_minute(merge_ticket_film_customer)

In [70]:
merge_ticket_film_customer[["duration_minute", "min"]] = merge_ticket_film_customer["duration"].str.split(" ", expand=True)

In [71]:
merge_ticket_film_customer["customer_amounts"] = merge_ticket_film_customer["slot type"].apply(calculate_customer)

In [72]:
merge_ticket_film_customer["birthday"] = merge_ticket_film_customer["DOB"].dt.strftime('%d-%m')

In [73]:
merge_ticket_film_customer["show_date"] = merge_ticket_film_customer["date_time"].dt.strftime('%d-%m')

In [74]:
merge_ticket_film_customer['is_go_on_birthday'] = (merge_ticket_film_customer['birthday'] == merge_ticket_film_customer['show_date']).astype(int)

In [75]:
merge_ticket_film_customer["month_of_birth"] = merge_ticket_film_customer["DOB"].dt.strftime('%m')

In [76]:
merge_ticket_film_customer["Customers"] = 'Customers'

In [77]:
detail = pd.DataFrame(merge_ticket_film_customer[["saledate", "date_time", "time", "time_diff_minute", "customerid", "orderid", "slot type", "customer_amounts", "cashier", "ticketcode", "film", "ticket price", "Gen", "popcorn", "Group", "country", "duration_minute", "rating", "listed_in", "Age", "birthday", "show_date", "is_go_on_birthday", "month_of_birth", "Customers"]])

In [78]:
detail = turn_column_name_into_same_format(detail)

In [79]:
detail[["listed_in_1", "listed_in_2", "listed_in_3", "listed_in_4", "listed_in_5"]] = detail["listed_in"].str.split(', ', expand=True)

In [80]:
group_list_in_1 = list(detail.groupby(["listed_in_1"]).groups.keys())
group_list_in_2 = list(detail.groupby(["listed_in_2"]).groups.keys())
group_list_in_3 = list(detail.groupby(["listed_in_3"]).groups.keys())
group_list_in_4 = list(detail.groupby(["listed_in_4"]).groups.keys())
group_list_in_5 = list(detail.groupby(["listed_in_5"]).groups.keys())

In [81]:
merge_list_in = merge_lists_without_duplicates(group_list_in_1, group_list_in_2)
merge_list_in = merge_lists_without_duplicates(merge_list_in, group_list_in_3)
merge_list_in = merge_lists_without_duplicates(merge_list_in, group_list_in_4)
merge_list_in = merge_lists_without_duplicates(merge_list_in, group_list_in_5)

In [82]:
for list_in in merge_list_in:
    detail[list_in] = detail.apply(lambda row: create_list_in_column(row, list_in), axis=1)

In [83]:
drop_column = ['listed_in_1', 'listed_in_2', 'listed_in_3', 'listed_in_4', 'listed_in_5']

In [84]:
detail.drop(columns=drop_column,inplace=True)

In [85]:
detail["ticket_price"] = detail["ticket_price"].astype(int)

In [86]:
detail["show_hour"] = detail["time"].apply(get_hour)

In [87]:
list_ticket_price = list(detail.groupby(['ticket_price']).groups.keys())

In [88]:
def create_ticket_column(row, ticket):
    if row['ticket_price'] == ticket: return 1
    else: return 0

In [89]:
for ticket in list_ticket_price:
    detail[ticket] = detail.apply(lambda row: create_ticket_column(row, ticket), axis=1)

In [90]:
detail.drop(columns={0}, inplace=True)

**COHORT ANALYSIS**

In [91]:
merge_ticket_film_customer['week'] = merge_ticket_film_customer['date_time'].dt.isocalendar().week

In [92]:
merge_ticket_film_customer['cohort_week'] = merge_ticket_film_customer.groupby('customerid')['date_time'].transform('min').dt.isocalendar().week

In [93]:
merge_ticket_film_customer = calculate_retention_rate(merge_ticket_film_customer)

C:\Users\DELL\AppData\Local\Temp\ipykernel_7692\3767804429.py:8: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0.15' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  dataframe.loc[(dataframe['cohort_week'] == cohort_week) & (dataframe['week'] == week), 'retention_rate'] = retention_rate


In [94]:
merge_ticket_film_customer["period_number"] = merge_ticket_film_customer["week"] - merge_ticket_film_customer["cohort_week"]

**FILM SUGGESTION**

In [95]:
showed_film = list(detail.groupby("film").groups.keys())

In [96]:
film_suggest = pd.DataFrame(film[["film", "duration", "listed_in", "rating", "country"]])

In [97]:
for value_to_drop in showed_film:
    film_suggest = film_suggest[film_suggest['film'] != value_to_drop]

In [98]:
film_suggest[["duration_minute", "min"]] = film_suggest["duration"].str.split(" ", expand=True)

In [99]:
film_suggest = film_suggest.drop(columns={"min"})

In [100]:
film_suggest = film_suggest.drop(columns={"duration"})

In [101]:
excel_file_path = 'D:\\Data\\Check\\detail.xlsx'
with pd.ExcelWriter(excel_file_path, engine='xlsxwriter') as writer:
    # Write each DataFrame to a different sheet
    detail.to_excel(writer, sheet_name='detail', index=False)
    film_suggest.to_excel(writer, sheet_name='film suggest', index=False)